In [1]:
!pip install gym_super_mario_bros==7.3.0 nes_py

  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
    Preparing wheel metadata: started
    Preparing wheel metadata: finished with status 'done'
  Created wheel for nes-py: filename=nes_py-8.1.8-cp38-cp38-win_amd64.whl size=47358 sha256=d54f03c0d68a26ed6f4da09f260c936712ae44e9b3a698cbeccabdabd3346088
  Stored in directory: c:\users\computing\appdata\local\pip\cache\wheels\8d\6e\f0\113c979eba40def28ee9b3c81a4adec00386106d81fb3bc2c2
  Created wheel for gym: filename=gym-0.23.1-py3-none-any.whl size=701357 sha256=4a041ac915ad36bd0ba3fda0f0513aabf58d9dba1c84ed6b4bffe3a0fe4057f1
  Stored in directory: c:\users\computing\appdata\local\pip\cache\wheels\78\28\77\b0c74e80a2a4faae0161d5c53bc4f8e436e77aedc79136ee13
Successfully built nes-py gym
  Attempting uninstall: importlib-metadata
    Found existing installation: importlib-met

In [2]:
# Install pytorch
!pip install torch==1.10.1+cu113 torchvision==0.11.2+cu113 torchaudio===0.10.1+cu113 -f https://download.pytorch.org/whl/cu113/torch_stable.html

Looking in links: https://download.pytorch.org/whl/cu113/torch_stable.html
  Attempting uninstall: torch
    Found existing installation: torch 1.9.1
    Uninstalling torch-1.9.1:
      Successfully uninstalled torch-1.9.1
  Attempting uninstall: torchvision
    Found existing installation: torchvision 0.10.1
    Uninstalling torchvision-0.10.1:
      Successfully uninstalled torchvision-0.10.1
  Attempting uninstall: torchaudio
    Found existing installation: torchaudio 0.9.1
    Uninstalling torchaudio-0.9.1:
      Successfully uninstalled torchaudio-0.9.1


In [3]:
!pip install stable-baselines3[extra]

  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
    Preparing wheel metadata: started
    Preparing wheel metadata: finished with status 'done'
  Using cached google_auth_oauthlib-0.4.6-py2.py3-none-any.whl (18 kB)
  Using cached tensorboard_data_server-0.6.1-py3-none-any.whl (2.4 kB)
  Using cached pyasn1_modules-0.2.8-py2.py3-none-any.whl (155 kB)
  Using cached pyasn1-0.4.8-py2.py3-none-any.whl (77 kB)
  Created wheel for gym: filename=gym-0.21.0-py3-none-any.whl size=1616823 sha256=293e50940b10b52a224579558eec64144caaf732876ac53df3ff817677295604
  Stored in directory: c:\users\computing\appdata\local\pip\cache\wheels\27\6d\b3\a3a6e10704795c9b9000f1ab2dc480dfe7bed42f5972806e73
  Created wheel for AutoROM.accept-rom-license: filename=AutoROM.accept_rom_license-0.4.2-py3-none-any.whl size=446447 sha256=9a6353e62f1389eb5

In [4]:
# Import the game
import gym_super_mario_bros
# Import the Joypad wrapper
from nes_py.wrappers import JoypadSpace
# Import the SIMPLIFIED controls
from gym_super_mario_bros.actions import SIMPLE_MOVEMENT
from stable_baselines3.common.callbacks import BaseCallback

In [5]:
# Setup game
env = gym_super_mario_bros.make('SuperMarioBros-v0')
env = JoypadSpace(env, SIMPLE_MOVEMENT)

In [6]:
# Setup game
env = gym_super_mario_bros.make('SuperMarioBros-v0')
env = JoypadSpace(env, SIMPLE_MOVEMENT)

In [7]:
class TrainAndLoggingCallback(BaseCallback):

    def __init__(self, check_freq, save_path, verbose=1):
        super(TrainAndLoggingCallback, self).__init__(verbose)
        self.check_freq = check_freq
        self.save_path = save_path

    def _init_callback(self):
        if self.save_path is not None:
            os.makedirs(self.save_path, exist_ok=True)

    def _on_step(self):
        if self.n_calls % self.check_freq == 0:
            model_path = os.path.join(self.save_path, 'best_model_{}'.format(self.n_calls))
            self.model.save(model_path)

        return True

In [8]:
CHECKPOINT_DIR = './train/'
LOG_DIR = './logs/'

In [9]:
# Setup model saving callback
callback = TrainAndLoggingCallback(check_freq=10000, save_path=CHECKPOINT_DIR)

In [10]:
# Import Frame Stacker Wrapper and GrayScaling Wrapper
from gym.wrappers import GrayScaleObservation
# Import Vectorization Wrappers
from stable_baselines3.common.vec_env import VecFrameStack, DummyVecEnv
# Import Matplotlib to show the impact of frame stacking
from matplotlib import pyplot as plt

In [11]:
# Import os for file path management
import os 
# Import PPO for algos
from stable_baselines3 import PPO
# Import Base Callback for saving models
from stable_baselines3.common.callbacks import BaseCallback

In [14]:
model = PPO('CnnPolicy', env, verbose=1, tensorboard_log=LOG_DIR, learning_rate=0.000001,seed=44,n_steps=512) 

Using cuda device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Wrapping the env in a VecTransposeImage.


In [15]:
model.learn(total_timesteps=2000000, callback=callback)

Logging to ./logs/PPO_2
----------------------------
| time/              |     |
|    fps             | 276 |
|    iterations      | 1   |
|    time_elapsed    | 1   |
|    total_timesteps | 512 |
----------------------------
-------------------------------------------
| time/                   |               |
|    fps                  | 152           |
|    iterations           | 2             |
|    time_elapsed         | 6             |
|    total_timesteps      | 1024          |
| train/                  |               |
|    approx_kl            | 5.4926495e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.95         |
|    explained_variance   | 0.00276       |
|    learning_rate        | 1e-06         |
|    loss                 | 149           |
|    n_updates            | 10            |
|    policy_gradient_loss | -0.000332     |
|    value_loss           | 463           |
-------------------------

-------------------------------------------
| time/                   |               |
|    fps                  | 112           |
|    iterations           | 13            |
|    time_elapsed         | 59            |
|    total_timesteps      | 6656          |
| train/                  |               |
|    approx_kl            | 0.00011056429 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.94         |
|    explained_variance   | 0.00842       |
|    learning_rate        | 1e-06         |
|    loss                 | 101           |
|    n_updates            | 120           |
|    policy_gradient_loss | 0.000337      |
|    value_loss           | 209           |
-------------------------------------------
-------------------------------------------
| time/                   |               |
|    fps                  | 112           |
|    iterations           | 14            |
|    time_elapsed         | 63  

-------------------------------------------
| time/                   |               |
|    fps                  | 108           |
|    iterations           | 24            |
|    time_elapsed         | 112           |
|    total_timesteps      | 12288         |
| train/                  |               |
|    approx_kl            | 1.4307676e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.94         |
|    explained_variance   | 0.0141        |
|    learning_rate        | 1e-06         |
|    loss                 | 0.596         |
|    n_updates            | 230           |
|    policy_gradient_loss | -0.000259     |
|    value_loss           | 1.43          |
-------------------------------------------
-------------------------------------------
| time/                   |               |
|    fps                  | 108           |
|    iterations           | 25            |
|    time_elapsed         | 117 

-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1.4e+04       |
|    ep_rew_mean          | 718           |
| time/                   |               |
|    fps                  | 108           |
|    iterations           | 34            |
|    time_elapsed         | 160           |
|    total_timesteps      | 17408         |
| train/                  |               |
|    approx_kl            | 1.6801758e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.94         |
|    explained_variance   | 0.182         |
|    learning_rate        | 1e-06         |
|    loss                 | 0.127         |
|    n_updates            | 330           |
|    policy_gradient_loss | 0.000206      |
|    value_loss           | 1.03          |
-------------------------------------------
------------------------------------------
| rollout/                |      

-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1.4e+04       |
|    ep_rew_mean          | 718           |
| time/                   |               |
|    fps                  | 107           |
|    iterations           | 43            |
|    time_elapsed         | 204           |
|    total_timesteps      | 22016         |
| train/                  |               |
|    approx_kl            | 6.0609542e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.94         |
|    explained_variance   | 0.0354        |
|    learning_rate        | 1e-06         |
|    loss                 | 0.0802        |
|    n_updates            | 420           |
|    policy_gradient_loss | -0.000566     |
|    value_loss           | 0.176         |
-------------------------------------------
------------------------------------------
| rollout/                |      

...

----------------------------------------
| rollout/                |            |
|    ep_len_mean          | 1.14e+03   |
|    ep_rew_mean          | 2.09e+03   |
| time/                   |            |
|    fps                  | 105        |
|    iterations           | 3859       |
|    time_elapsed         | 18751      |
|    total_timesteps      | 1975808    |
| train/                  |            |
|    approx_kl            | 0.00292584 |
|    clip_fraction        | 0.015      |
|    clip_range           | 0.2        |
|    entropy_loss         | -0.252     |
|    explained_variance   | 0.598      |
|    learning_rate        | 1e-06      |
|    loss                 | 147        |
|    n_updates            | 38580      |
|    policy_gradient_loss | 0.00236    |
|    value_loss           | 739        |
----------------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.14e+03    |
|    ep_rew_m

-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1.12e+03      |
|    ep_rew_mean          | 2.07e+03      |
| time/                   |               |
|    fps                  | 105           |
|    iterations           | 3869          |
|    time_elapsed         | 18800         |
|    total_timesteps      | 1980928       |
| train/                  |               |
|    approx_kl            | 0.00026054622 |
|    clip_fraction        | 0.000391      |
|    clip_range           | 0.2           |
|    entropy_loss         | -0.241        |
|    explained_variance   | 0.831         |
|    learning_rate        | 1e-06         |
|    loss                 | 38.7          |
|    n_updates            | 38680         |
|    policy_gradient_loss | -0.00056      |
|    value_loss           | 90.6          |
-------------------------------------------
------------------------------------------
| rollout/                |      

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.13e+03    |
|    ep_rew_mean          | 2.1e+03     |
| time/                   |             |
|    fps                  | 105         |
|    iterations           | 3879        |
|    time_elapsed         | 18848       |
|    total_timesteps      | 1986048     |
| train/                  |             |
|    approx_kl            | 0.004225086 |
|    clip_fraction        | 0.0166      |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.356      |
|    explained_variance   | 0.877       |
|    learning_rate        | 1e-06       |
|    loss                 | 66          |
|    n_updates            | 38780       |
|    policy_gradient_loss | -0.00163    |
|    value_loss           | 176         |
-----------------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.13

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.15e+03    |
|    ep_rew_mean          | 2.1e+03     |
| time/                   |             |
|    fps                  | 105         |
|    iterations           | 3889        |
|    time_elapsed         | 18899       |
|    total_timesteps      | 1991168     |
| train/                  |             |
|    approx_kl            | 0.004024652 |
|    clip_fraction        | 0.0191      |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.477      |
|    explained_variance   | 0.899       |
|    learning_rate        | 1e-06       |
|    loss                 | 162         |
|    n_updates            | 38880       |
|    policy_gradient_loss | -0.000745   |
|    value_loss           | 396         |
-----------------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.15

------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.15e+03     |
|    ep_rew_mean          | 2.11e+03     |
| time/                   |              |
|    fps                  | 105          |
|    iterations           | 3899         |
|    time_elapsed         | 18948        |
|    total_timesteps      | 1996288      |
| train/                  |              |
|    approx_kl            | 0.0017189564 |
|    clip_fraction        | 0.0109       |
|    clip_range           | 0.2          |
|    entropy_loss         | -0.145       |
|    explained_variance   | 0.845        |
|    learning_rate        | 1e-06        |
|    loss                 | 39.2         |
|    n_updates            | 38980        |
|    policy_gradient_loss | -0.00267     |
|    value_loss           | 125          |
------------------------------------------
-------------------------------------------
| rollout/                |               |
|    ep_l

In [16]:
model.save("seed42ppomodel")